# Apples and Oranges

Use `:help` to get an overview for the jupyter notebook commands. If you need more insight on how to use this tool, consider reading *ProB Jupyter Notebook Overview*.

This puzzle is [apparently an Interview question at Apple](https://bgr.com/2015/11/20/apple-interview-questions/). Quoting from
[1](https://bgr.com/2015/11/20/apple-interview-questions/) we have the
following information:

* (1) There are three boxes, one contains only apples, one contains only oranges, and one contains both apples and oranges.
* (2) The boxes have been incorrectly labeled such that no label identifies the actual contents of the box it labels.
* (3) Opening just one box, and without looking in the box, you take out one piece of fruit.
* (4) By looking at the fruit, how can you immediately label all of the boxes correctly?

Here is one encoding of this puzzle in B:


In [1]:
::load
MACHINE ApplesOranges
SETS
 Fruit={apple,orange}; // possible content for the boxes
 Label={A,O,Both} // labels for the boxes
CONSTANTS a,o,b,  // a,o,b are the three boxes
          Take,  // which box should we open (the label of that box)
          DecisionFunction // given the fruit we pick from Take: what are the contents of the boxes labeled A,O,Both
PROPERTIES
  a = {apple} & o={orange} & b={apple,orange} // (1)
  &
  Take : Label //3
  &
  DecisionFunction : Fruit --> (Label >->> {a,o,b}) & //4
  !label. ( // the decision function has to work for all allowed labelings
  ( label : {a,o,b} >->> Label &
    label(a) /= A & label(o) /= O & label(b) /= Both // (2)
  )
   =>
  !f.(f: label~(Take)
      => DecisionFunction(f)=label~ // the function should tell us what is behind label A,O,Both
     )
  )
END

Loaded machine: ApplesOranges

We have abstracted the box of apples `a` by the set containing `apple`.
Ditto for `o` and `b`, which are abstracted by `{orange}` and
`{apple,orange}` respectively.

NOTE: You need a recent version of ProB 1.5.1-beta3 or newer to load the above model on your own computer with its one-line comments. If you have an older version of ProB, simply use the normal comments `/* ... */`.

`:goto Number` jumps to the state with the given number. 

With the `:trace` command, you will get the information of your current trace.

There is an autocompletion tool, which allows you to see the possible commands, simply use TAB after you type in your `:`. 

This model gives you just one solution, after setting up the constants with `:constants`.

In [2]:
:goto -1

Changed to state with index -1

In [3]:
:trace

* -1: Root state **(current)**

In [4]:
:constants

Machine constants set up using operation 0: $setup_constants()

In [5]:
Take

$\mathit{Both}$

As we can see, the only solution is to open the box labelled with
"Both". We can inspect the decision function by using the jupyter notebook code block, like follows:

In [6]:
DecisionFunction(apple)

$\{(\mathit{A}\mapsto\{\mathit{orange}\}),(\mathit{O}\mapsto\{\mathit{apple},\mathit{orange}\}),(\mathit{Both}\mapsto\{\mathit{apple}\})\}$

In [7]:
DecisionFunction(orange)

$\{(\mathit{A}\mapsto\{\mathit{apple},\mathit{orange}\}),(\mathit{O}\mapsto\{\mathit{apple}\}),(\mathit{Both}\mapsto\{\mathit{orange}\})\}$

In other words, when we pick an apple out of the box labelled with
"Both", then it contains only apples and the box labelled "O"ranges
contains both apples and oranges. The box labelled "A"pples contains
just oranges. Similarly, if we pick up an orange out of the box labelled
with "Both", then it contains only oranges and the box labelled with
"A"pples contains contains both apples and oranges. The box labelled
"O"ranges contains just apples.

NOTE: You can use `:table Expression` to get values or expressions in a tabular form.

In [8]:
:table DecisionFunction

|prj1|prj2|
|---|---|
|$\mathit{apple}$|$\{(\mathit{A}\mapsto\{\mathit{orange}\}),(\mathit{O}\mapsto\{\mathit{apple},\mathit{orange}\}),(\mathit{Both}\mapsto\{\mathit{apple}\})\}$|
|$\mathit{orange}$|$\{(\mathit{A}\mapsto\{\mathit{apple},\mathit{orange}\}),(\mathit{O}\mapsto\{\mathit{apple}\}),(\mathit{Both}\mapsto\{\mathit{orange}\})\}$|


## Argumentation Theory



Below we try to model some concepts of argumentation theory in B. The examples try to show that classical (monotonic) logic with set theory can be used to model some aspects of argumentation theory quite naturally, and that ProB can solve and visualise some problems in argumentation theory. Alternative solutions are encoding arguments as normal logic programs (with non-monotonic negation) and using answer set solvers for problem solving.

The following model was inspired by a talk given by Claudia Schulz.

The model below represents the labelling of the arguments as a total function from arguments to its status, which can either be in (the argument is accepted), out (the argument is rejected), or undec (the argument is undecided). The relation between the arguments is given in the binary attacks relation.

In case you are new to B, you probably need to know the following operators to understand the specification below (we als have a summary page about the B syntax in our handbook):

* `x : S` specifies that x is an element of S
* `a|→b` represents the pair (a,b); note that a relation and function in B is a set of pairs.
* 